# **PROJECT-3. EDA + Feature Engineering. Соревнование на Kaggle**

In [19]:
# БИБЛИОТЕКИ

import pandas as pd 
pd.options.mode.chained_assignment = None  # default='warn'
import numpy as np
import re
import seaborn as sns
from geopy.distance import geodesic as GD # для работы с координатами
from matplotlib import pyplot as plt
from IPython.display import display
import logging
from comet_ml import Experiment
import random


from sklearn.linear_model import LogisticRegression
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import accuracy_score

# Загружаем специальный инструмент для разбивки:  
from sklearn.model_selection import train_test_split
# Импортируем необходимые библиотеки для обучения модели:  
from sklearn.ensemble import RandomForestRegressor # инструмент для создания и обучения модели  
from sklearn import metrics # инструменты для оценки точности модели  

ОПИСАНИЕ ДАННЫХ

1. **hotel_address** — адрес отеля;
2. **review_date** — дата, когда рецензент разместил соответствующий отзыв;
3. **average_score** — средний балл отеля, рассчитанный на основе последнего комментария за последний год;
4. **hotel_name** — название отеля;
5. **reviewer_nationality** — страна рецензента;
6. **negative_review** — отрицательный отзыв, который рецензент дал отелю;
7. **review_total_negative_word_counts** — общее количество слов в отрицательном отзыв;
8. **positive_review** — положительный отзыв, который рецензент дал отелю;
9. **review_total_positive_word_counts** — общее количество слов в положительном отзыве.
10. **reviewer_score** — оценка, которую рецензент поставил отелю на основе своего опыта;
11. **total_number_of_reviews_reviewer_has_given** — количество отзывов, которые рецензенты дали в прошлом;
12. **total_number_of_reviews** — общее количество действительных отзывов об отеле;
13. **tags** — теги, которые рецензент дал отелю;
14. **days_since_review** — количество дней между датой проверки и датой очистки;
15. **additional_number_of_scoring** — есть также некоторые гости, которые просто поставили оценку сервису, но не оставили отзыв. Это число указывает, сколько там действительных оценок без проверки.
16. **lat** — географическая широта отеля;
17. **lng** — географическая долгота отеля.

In [20]:
hotels = pd.read_csv('data/hotels.csv')
display(hotels.head(3))
display(hotels.info())

hotel_address  \
0  Stratton Street Mayfair Westminster Borough Lo...   
1  130 134 Southampton Row Camden London WC1B 5AF...   
2   151 bis Rue de Rennes 6th arr 75006 Paris France   

   additional_number_of_scoring review_date  average_score  \
0                           581   2/19/2016            8.4   
1                           299   1/12/2017            8.3   
2                            32  10/18/2016            8.9   

                          hotel_name reviewer_nationality  \
0                 The May Fair Hotel      United Kingdom    
1    Mercure London Bloomsbury Hotel      United Kingdom    
2  Legend Saint Germain by Elegancia               China    

       negative_review  review_total_negative_word_counts  \
0             Leaving                                   3   
1       poor breakfast                                  3   
2   No kettle in room                                   6   

   total_number_of_reviews      positive_review  \
0                     1994   Staff were amazing   
1                     1361             location   
2                      406          No Positive   

   review_total_positive_word_counts  \
0                                  4   
1                                  2   
2                                  0   

   total_number_of_reviews_reviewer_has_given  reviewer_score  \
0                                           7            10.0   
1                                          14             6.3   
2                                          14             7.5   

                                                tags days_since_review  \
0  [' Leisure trip ', ' Couple ', ' Studio Suite ...           531 day   
1  [' Business trip ', ' Couple ', ' Standard Dou...           203 day   
2  [' Leisure trip ', ' Solo traveler ', ' Modern...           289 day   

         lat       lng  
0  51.507894 -0.143671  
1  51.521009 -0.123097  
2  48.845377  2.325643

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 386803 entries, 0 to 386802
Data columns (total 17 columns):
 #   Column                                      Non-Null Count   Dtype  
---  ------                                      --------------   -----  
 0   hotel_address                               386803 non-null  object 
 1   additional_number_of_scoring                386803 non-null  int64  
 2   review_date                                 386803 non-null  object 
 3   average_score                               386803 non-null  float64
 4   hotel_name                                  386803 non-null  object 
 5   reviewer_nationality                        386803 non-null  object 
 6   negative_review                             386803 non-null  object 
 7   review_total_negative_word_counts           386803 non-null  int64  
 8   total_number_of_reviews                     386803 non-null  int64  
 9   positive_review                             386803 non-null  object 
 

None

***
## **Создание и преобразвание признаков**

### **Признак hotel_address**

- возможно получить страну отеля (новый признак - 'country_of_hotel')
- возможно получить город из страны отеля (новый признак - 'city_of_hotel')

In [21]:
# получим страну и город из адреса отеля

# составим список всех стран из признака национальности автора обзора
country_set = set(hotels['reviewer_nationality'].str.strip())
country_set.remove('')
display(len(country_set)) # - всего 224 страны, этого должно хватить для вычленения страны из признака адреса отеля

# Функция для поиска страны с конца строки в нашем датафрейме
def get_countries(strs, countries):
    countries_series = []
    for string in strs:
        for country in countries:
            if country in ' '.join(string.split()[-2:]):
                countries_series.append(country)
    countries_series = pd.Series(countries_series)
    return countries_series

country_of_hotel = get_countries(hotels['hotel_address'],country_set)
hotels['country_of_hotel'] = country_of_hotel
display(country_of_hotel.value_counts())

224

United Kingdom    196774
Spain              45132
France             44830
Netherlands        43006
Austria            29178
Italy              27883
dtype: int64

In [22]:
# функция для поиска города отеля
def get_cities(strs,country):
    cities_series = []
    for string in range(0,strs.shape[0]):
        if country.iloc[string]=='United Kingdom':
            cities_series.append(''.join(strs.iloc[string].split()[-5:-2][0]))
        else:
            cities_series.append(''.join(strs.iloc[string].split()[-5:][3]))
    cities_series = pd.Series(cities_series)
    return cities_series

city_of_hotel = get_cities(hotels['hotel_address'],hotels['country_of_hotel'])
hotels['city_of_hotel'] = city_of_hotel
display(city_of_hotel.value_counts())

London       196774
Barcelona     45132
Paris         44830
Amsterdam     43006
Vienna        29178
Milan         27883
dtype: int64

### **Признак latitude-longitude**

- можем вычислить примерное расстояние до центра города от отеля (новый признак - 'distance_to_citycenter')

In [23]:
# создадим признаки координат центра города (инфа взята с сайта https://www.gps-coordinates.net/)
latitude_by_city={'London':51.5073219,'Barcelona':41.3828939,'Paris':48.8588897,'Amsterdam':52.3727598,'Vienna':48.2083537,'Milan':45.4641943}
longitude_by_city={'London':-0.1276474,'Barcelona':2.1774322,'Paris':2.320041,'Amsterdam':4.8936041,'Vienna':16.3725042,'Milan':9.1896346}

# широта координат центра города
latitude_by_city_list=[]
for i in range(0,hotels.shape[0]):
    for key, value in latitude_by_city.items():
        if key==hotels['city_of_hotel'][i]:
            latitude_by_city_list.append(value)
hotels['latitude_by_city']=latitude_by_city_list
# долгота координат центра города
longitude_by_city_list=[]
for i in range(0,hotels.shape[0]):
    for key, value in longitude_by_city.items():
        if key==hotels['city_of_hotel'][i]:
            longitude_by_city_list.append(value)
hotels['longitude_by_city']=longitude_by_city_list

# функция вычисления расстояния от отеля до центра города
def get_center_dist(lat_1,long_1,lat_2,long_2):
    distance = []
    for i in range(0,lat_1.shape[0]):
        if not np.isnan(lat_1[i]):
            distance.append(GD((lat_1[i],long_1[i]), (lat_2[i],long_2[i])).km)
        else:
            distance.append(np.nan)
    return distance

# используем функцию и запишем полученные значения в таблицу
distance_to_citycenter = get_center_dist(hotels['lat'],hotels['lng'],hotels['latitude_by_city'],hotels['longitude_by_city'])
hotels['distance_to_citycenter'] = distance_to_citycenter

# заполним оставшиеся 2448 значений (ровно столько пустых широт) по среднему расстоянию до центра в зависимости от города
mean_dists = dict(hotels.groupby(['city_of_hotel']).mean()['distance_to_citycenter'])
hotels['distance_to_citycenter'] = hotels.set_index('city_of_hotel')['distance_to_citycenter'].fillna(mean_dists).reset_index()['distance_to_citycenter']
display(hotels['distance_to_citycenter'].value_counts())

7.275664    3587
0.631031    3206
1.044115    3095
4.542343    2688
3.465016    2379
            ... 
6.311114       7
3.201518       7
6.575847       6
2.747701       6
4.619540       5
Name: distance_to_citycenter, Length: 1475, dtype: int64

### **Признак reviewer_nationality**

* можем создать дополнительный признак для отеля по популярности среди туристов (количетсво уникальных стран, из которых туристы писали отзывы для определенного отеля)

In [35]:
hotel_popularity = dict(hotels.groupby('hotel_name')['reviewer_nationality'].nunique())
# теперь каждому отелю соответствует число, показывающее туристы из скольких разных стран выбирают его
hotels["hotel_popularity"]=hotels['hotel_name'].replace(hotel_popularity)

In [25]:
# удалим лишние признаки: (hotel_adress, hotel_name, lat, lng, city_of_hotel, latitude_by_city, longitude_by_city)

#hotels.drop(['hotel_address', 'hotel_name', 'lat', 'lng', 'city_of_hotel','latitude_by_city', 'longitude_by_city'], axis=1, inplace=True)

### **Признак tags**

- можем создать бинарный признак по типу поездки по наличию тега **'Leisure trip'** или **'Business_trip'** в обзоре (новый признак - 'trip_type'), где 0 - отдых, 1 - деловая поездка
- можем создать бинарный признак по наличию тегов **'Family with young children'** и **'Family with older children'** в обзоре (новый признак - 'family'), где 0 - отсутствие, а 1 - наличие данного тэга
- можем создать признак по тегу **'Stayed ** nights'** в обзоре (новый признак - 'stayed_for'), основанный на количестве дней от 1 до 8, где цифры 1-7 - соответствующее количество дней, а 8 - всё, что больше семи дней
- можем создать признак по тегам **'solo'**, **'couple'**, **'group'** в обзоре (новый признак - 'group_type'), основанный на количестве людей в группе, от 1 до 3, где 1, 2, 3 - соло, пара, группа
-  можем создать признак по тегам **'Standard ...', 'Superior ...', 'Deluxe ...', 'Executive ...', и т. д.** в обзоре (новый признак - 'room_type'), основанный на категории комнаты

In [26]:
# форматируем строки с тегами в нормальные списки для удобства обработки
regex = """\'\s(.*?)\s\'""" # регулярное выражение
hotels['tags'] = hotels['tags'].str.findall(regex)

In [27]:
# создаём новый признак trip_type по типу поездки
hotels['trip_type'] = np.nan
for i in range(0,hotels.shape[0]):
    if 'Leisure trip' in hotels['tags'][i]:
        hotels['trip_type'][i]= 0
    elif 'Business trip' in hotels['tags'][i]:
        hotels['trip_type'][i]= 1
    else:
        hotels['trip_type'][i]= np.nan

# заполним пропуски (3 % записей - Nan значения) случайным выбором между 0 и 1
hotels['trip_type'].fillna(random.choice(hotels['trip_type'][hotels['trip_type'].notna()]), inplace=True)
hotels['trip_type'] = hotels['trip_type'].astype('int32')
display(hotels['trip_type'].value_counts())

0    324814
1     61989
Name: trip_type, dtype: int64

In [28]:
# создаём новый признак family для обзорщиков, заселявшихся с семьёй
hotels['family'] = np.nan
for i in range(0,hotels.shape[0]):
    if ('Family with older children' in hotels['tags'][i]) or ('Family with young children' in hotels['tags'][i]):
        hotels['family'][i]= 1
    else:
        hotels['family'][i]= 0
hotels['family'] = hotels['family'].astype(int)
hotels['family'].value_counts()

0    321165
1     65638
Name: family, dtype: int64

In [29]:
# создаём признак stayed_for по количеству дней
nights = [] # сюда запишем вычлененные теги
for i in range(0,hotels.shape[0]):
    nights.append(",".join(s for s in hotels['tags'][i] if 'Stayed '.lower() in s.lower()))
hotels['stayed_for'] = nights
hotels['stayed_for'] = hotels['stayed_for'].str.findall('\S+\s(\d*)').apply(', '.join)
# заполняем 146 пропусков наиболее часто встречающимся тегом - 1 день
for i in range(0,hotels.shape[0]):
    if hotels['stayed_for'][i]=='':
        hotels['stayed_for'][i]='1'
hotels['stayed_for'] = hotels['stayed_for'].astype(int)
# преобразуем всё, что больше 7 в 8
for i in range(0,hotels.shape[0]):
    if hotels['stayed_for'][i]>7:
        hotels['stayed_for'][i]=8
hotels['stayed_for'].value_counts()

1    145519
2    100263
3     72000
4     35748
5     15611
6      7399
7      5549
8      4714
Name: stayed_for, dtype: int64

In [30]:
# создаём признак group_type по размеру группы
hotels['group_type'] = np.nan
for i in range(0,hotels.shape[0]):
    if 'Solo traveler' in hotels['tags'][i]:
        hotels['group_type'][i]= 1
    elif 'Couple' in hotels['tags'][i]:
        hotels['group_type'][i]= 2
    elif 'Group' in hotels['tags'][i]:
        hotels['group_type'][i]= 3
    else:
        hotels['group_type'][i]= np.nan

# заполним пропуски: там, где стоит тег "семья" или "путешествие с друзьями"- это явно группа (цифра 3) 
for i in range(0,hotels.shape[0]):
    if (pd.isna(hotels['group_type'][i]) and ((hotels['family'][i]==1) or ('Travelers with friends' in hotels['tags'][i]))):
        hotels['group_type'][i]=3

hotels['group_type'] = hotels['group_type'].astype('int32')
hotels['group_type'].value_counts()

2    189212
3    116356
1     81235
Name: group_type, dtype: int64

In [31]:
# создаём признак room_type по категории номера
rooms = hotels['tags'].apply(', '.join) # сюда запишем вычлененные теги
regex = 'Deluxe.*?Room.*?,|Classic.*?Room.*?,|Superior.*?Room.*?,|Executive.*?Room.*?,|Standard.*?Room.*?,|Double.*?Room.*?,|Twin.*?Room.*?,'
rooms = rooms.str.findall(regex, re.I).apply(', '.join)
rooms = rooms.str.replace(',','').str.lower()
rooms = rooms.str.split()
for i in range(0,rooms.shape[0]):
    if rooms[i]==[]:
        rooms[i]='standard'
    for item in rooms[i]:
        if item in ['deluxe','classic','superior','executive','standard','double','twin']:
            rooms[i]=item

hotels['room_type'] = rooms

In [32]:
# удаляем лишние столбцы: (tags)

#hotels.drop(['tags'], axis=1, inplace=True)

### **ДУБЛИКАТЫ**

Имеющиеся в датасете дублирующиеся строки удаляем методом *dropduplicates*

In [33]:
print(hotels.duplicated(subset=hotels.columns).value_counts())
hotels.drop_duplicates(inplace=True)
print(f'Результирующее число записей: {hotels.shape[0]}')

TypeError: unhashable type: 'list'

In [ ]:
from pandas_profiling import ProfileReport
#profile = ProfileReport(hotels, title="Hotels Profiling Report")
#profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]